## 📌 How many conversations related to fever? What proportion of total conversations?


In [1]:
from dotenv import load_dotenv
import os

# Cargar las variables de entorno desde el archivo .env
load_dotenv()

# Obtener las variables de entorno
db_name = os.getenv('DB_NAME')
db_user = os.getenv('DB_USER')
db_password = os.getenv('DB_PASSWORD')
db_host = os.getenv('DB_HOST')
db_port = os.getenv('DB_PORT')

import os
import pandas as pd
import psycopg2
from psycopg2 import sql
from dotenv import load_dotenv

def ejecutar_consulta(query, table_name):
    """
    Ejecuta una consulta SQL en la tabla especificada y devuelve un DataFrame de pandas.

    Parámetros:
    - query: str, consulta SQL con un marcador de posición para el nombre de la tabla.
    - table_name: str, nombre de la tabla a consultar.

    Retorna:
    - DataFrame de pandas con los resultados de la consulta.
    """
    # Cargar las variables de entorno desde el archivo .env
    load_dotenv()

    # Obtener las variables de entorno
    db_name = os.getenv('DB_NAME')
    db_user = os.getenv('DB_USER')
    db_password = os.getenv('DB_PASSWORD')
    db_host = os.getenv('DB_HOST')
    db_port = os.getenv('DB_PORT')

    try:
        # Establecer la conexión
        conexion = psycopg2.connect(
            dbname=db_name,
            user=db_user,
            password=db_password,
            host=db_host,
            port=db_port
        )
        print("Conexión exitosa a la base de datos")

        # Crear un cursor
        cursor = conexion.cursor()

        # Formatear la consulta con el nombre de la tabla
        consulta_formateada = sql.SQL(query).format(
            table=sql.Identifier(table_name)
        )

        # Ejecutar la consulta
        cursor.execute(consulta_formateada)

        # Obtener los nombres de las columnas
        nombres_columnas = [desc[0] for desc in cursor.description]

        # Cargar los resultados en un DataFrame de pandas
        df = pd.DataFrame(cursor.fetchall(), columns=nombres_columnas)

        # Establecer una columna como índice (opcional, aquí se asume que hay una columna 'id')
        if 'id' in df.columns:
            df.set_index('id', inplace=True)

        # Cerrar el cursor y la conexión
        cursor.close()
        conexion.close()
        print("Conexión cerrada")

        return df

    except psycopg2.Error as e:
        print(f"Error en la conexión o durante la ejecución de la consulta: {e}")
        return None


In [ ]:
import matplotlib.pyplot as plt

# Execute the query
consulta = """
WITH conversation_counts AS (
    SELECT 
        phone_id,
        COUNT(*) AS total_mensajes
    FROM "message whatsapp"
    GROUP BY phone_id
    HAVING COUNT(*) >= 6  -- Filter only conversations with at least 5 messages
)
SELECT 
    COUNT(DISTINCT cc.phone_id) AS total_conversaciones,
    COUNT(DISTINCT CASE WHEN mw.message ILIKE '%fiebre%' OR mw.message ILIKE '%temperatura%' OR mw.message ILIKE '%febril%' THEN mw.phone_id END) AS conversaciones_fiebre,
    COUNT(DISTINCT CASE WHEN mw.message ILIKE '%fiebre%' OR mw.message ILIKE '%temperatura%' OR mw.message ILIKE '%febril%' THEN mw.phone_id END) * 100.0 / COUNT(DISTINCT cc.phone_id) AS proporcion_fiebre
FROM "message whatsapp" mw
JOIN conversation_counts cc ON mw.phone_id = cc.phone_id;
"""
nombre_tabla = "message whatsapp"

df_fever_stats = ejecutar_consulta(consulta, nombre_tabla)

# Extract data
total_conversaciones = df_fever_stats["total_conversaciones"].iloc[0]
conversaciones_fiebre = df_fever_stats["conversaciones_fiebre"].iloc[0]
proporcion_fiebre = df_fever_stats["proporcion_fiebre"].iloc[0]

# Bar chart with numbers on top
plt.figure(figsize=(6, 6))  # Increase the height of the figure
bars = plt.bar(["Total historics", "Historics with fever"], [total_conversaciones, conversaciones_fiebre], color=['blue', 'red'])
plt.title(f'Proportion of historics with fever terms ({proporcion_fiebre:.2f}%)')
plt.ylabel("Number of historics")

# Add numbers on top of the bars
for bar in bars:
    yval = bar.get_height()
    plt.text(bar.get_x() + bar.get_width()/2, yval + 50, int(yval), ha='center', va='bottom')

plt.show()


## Load 100 conversations with almost 1000 messages

In [2]:
import pandas as pd

query_df = pd.read_json('100_historicos.json')
query_df

created_at  phone_id  origin type_message  \
0      2024-01-19 19:59:03.851000+00:00        13   agent         text   
1      2024-01-19 20:01:11.844000+00:00      5387   agent         text   
2      2024-01-19 20:01:15.860000+00:00      7003   agent         text   
3      2024-01-19 20:12:50.585000+00:00      5722   agent         text   
4      2024-01-19 20:12:58.576000+00:00      7145  client         text   
...                                 ...       ...     ...          ...   
213612 2024-12-31 04:43:22.874000+00:00     10076   agent         text   
213613 2024-12-31 04:44:47.115000+00:00      9450  client         text   
213614 2024-12-31 04:44:55.401000+00:00      9450  client         text   
213615 2024-12-31 04:59:15.216000+00:00       598  client         text   
213616 2024-12-31 04:59:38.917000+00:00       598  client         text   

                                                  message  
0                                             plantilla 9  
1                                             plantilla 9  
2                                             plantilla 9  
3                                             plantilla 9  
4       Gracias por comunicarte con E&C PUERTAS ELECTR...  
...                                                   ...  
213612  Listo listo, super que este mejor de la piel. ...  
213613                                               38.5  
213614                   Se despertó, debe tener malestar  
213615                       Tambien lo odia, que tortura  
213616  Me falta una pastilla, grita como si la estuvi...  

[213617 rows x 5 columns]

## Data preparation
Separete the data into different conversations, cleaning messages and conversations based on different rules.

In [3]:
# Delete all origin = 'bot' rows
query_df = query_df[query_df['origin'] != 'bot']

# Separate the data into historics (based on phone_id) and save historics into a list
historics = []
phone_ids = query_df['phone_id'].unique()
for phone_id in phone_ids:
    phone_historics = query_df[query_df['phone_id'] == phone_id]
    historics.append(phone_historics)

print('Amount of historics:', len(historics))

Amount of historics: 100


In [14]:
import pandas as pd
import os

def split_conversations(df):
    conversations = []  # List to store separated conversations
    current_conversation = []  # Temporary list to store current messages
    last_timestamp = None  # To track the time between messages

    # Define key criteria
    SALUDOS = ["hola", "buenos días", "buenos dias", "buenas tardes", "buenas noches", "buenas"]
    DESPEDIDAS = ["adios", "hasta luego", "nos vemos", "chao", "hasta pronto", "hasta mañana"]
    MAX_INACTIVITY_HOURS = 4  # Hours of inactivity to consider a new conversation
    MIN_MESSAGES = 15  # Minimum number of messages to consider a conversation

    for index, row in df.iterrows():
        message = row['message']
        created_at = pd.to_datetime(row['created_at'])

        # Convert message to lowercase for comparison
        message_lower = message.lower() if isinstance(message, str) else ""

        # Check if the message starts a conversation
        is_new_convo = (
            '{Docochat} ha asignado esta conversación a' in message_lower or
            any(saludo in message_lower for saludo in SALUDOS) or
            (last_timestamp and (created_at - last_timestamp).total_seconds() / 3600 > MAX_INACTIVITY_HOURS)
        )

        if is_new_convo:
            if current_conversation:
                # If the current conversation meets the minimum criteria, save it
                if len(current_conversation) >= MIN_MESSAGES:
                    conversations.append(pd.DataFrame(current_conversation))
                current_conversation = []

        # Add the current row to the conversation
        current_conversation.append(row)
        last_timestamp = created_at

        # Check if the message ends a conversation using multiple conditions
        is_end_convo = (
            'ha tipificado como {Cerrar}' in message_lower or
            any(despedida in message_lower for despedida in DESPEDIDAS) or
            (last_timestamp and (created_at - last_timestamp).total_seconds() / 3600 > MAX_INACTIVITY_HOURS and len(current_conversation) > MIN_MESSAGES)
        )

        if is_end_convo:
            if len(current_conversation) >= MIN_MESSAGES:
                conversations.append(pd.DataFrame(current_conversation))
            current_conversation = []

    # Save the last conversation if it meets the criteria
    if current_conversation and len(current_conversation) >= MIN_MESSAGES:
        conversations.append(pd.DataFrame(current_conversation))

    return conversations

# Apply the function to each historic and save them in json files

# Create the directory if it doesn't exist
# if not os.path.exists('conversations'):
#     os.makedirs('conversations')

# for i, historic in enumerate(historics):
#     conversations = split_conversations(historic)
#     phone_id = historic['phone_id'].iloc[0]
#     for j, conversation in enumerate(conversations):
#         conversation.to_json(f'conversations/phone_id_{phone_id}_conversation_{j}.json', orient='records')

# print('Conversations saved successfully')

In [4]:
import pandas as pd
import os

def split_conversations(df):
    conversations = []  # List to store separated conversations
    excluded_messages = []  # List to store excluded messages
    current_conversation = []  # Temporary list to store current messages
    last_timestamp = None  # To track the time between messages

    # Define key criteria
    SALUDOS = ["hola", "buenos días", "buenos dias", "buenas tardes", "buenas noches", "buenas"]
    DESPEDIDAS = ["adios", "hasta luego", "nos vemos", "chao", "hasta pronto", "hasta mañana"]
    MAX_INACTIVITY_HOURS = 4  # Hours of inactivity to consider a new conversation
    MIN_MESSAGES = 15  # Minimum number of messages to consider a conversation

    for index, row in df.iterrows():
        message = row['message']
        created_at = pd.to_datetime(row['created_at'])

        # Convert message to lowercase for comparison
        message_lower = message.lower() if isinstance(message, str) else ""

        # Check if the message starts a conversation
        is_new_convo = (
            '{Docochat} ha asignado esta conversación a' in message_lower or
            any(saludo in message_lower for saludo in SALUDOS) or
            (last_timestamp and (created_at - last_timestamp).total_seconds() / 3600 > MAX_INACTIVITY_HOURS)
        )

        if is_new_convo:
            if current_conversation:
                if len(current_conversation) >= MIN_MESSAGES:
                    conversations.append(pd.DataFrame(current_conversation))
                else:
                    excluded_messages.extend(current_conversation)  # Store excluded messages
                current_conversation = []

        # Add the current row to the conversation
        current_conversation.append(row)
        last_timestamp = created_at

        # Check if the message ends a conversation using multiple conditions
        is_end_convo = (
            'ha tipificado como {Cerrar}' in message_lower or
            any(despedida in message_lower for despedida in DESPEDIDAS) or
            (last_timestamp and (created_at - last_timestamp).total_seconds() / 3600 > MAX_INACTIVITY_HOURS and len(current_conversation) > MIN_MESSAGES)
        )

        if is_end_convo:
            if len(current_conversation) >= MIN_MESSAGES:
                conversations.append(pd.DataFrame(current_conversation))
            else:
                excluded_messages.extend(current_conversation)  # Store excluded messages
            current_conversation = []

    # Save the last conversation if it meets the criteria
    if current_conversation:
        if len(current_conversation) >= MIN_MESSAGES:
            conversations.append(pd.DataFrame(current_conversation))
        else:
            excluded_messages.extend(current_conversation)

    return conversations, pd.DataFrame(excluded_messages)

# Apply the function to each historic and save them in JSON files

# Create directories if they don't exist
if not os.path.exists('conversations'):
    os.makedirs('conversations')
if not os.path.exists('excluded_messages'):
    os.makedirs('excluded_messages')

for i, historic in enumerate(historics):
    conversations, excluded_df = split_conversations(historic)
    phone_id = historic['phone_id'].iloc[0]
    
    # Save conversations
    for j, conversation in enumerate(conversations):
        conversation.to_json(f'conversations/phone_id_{phone_id}_conversation_{j}.json', orient='records')
    
    # Save excluded messages
    if not excluded_df.empty:
        excluded_df.to_json(f'excluded_messages/phone_id_{phone_id}_excluded.json', orient='records')

print('Conversations and excluded messages saved successfully')

Conversations and excluded messages saved successfully


### Let's look some examples of conversations

In [7]:
# Conversation random of some phone_id
import random
pd.set_option('display.max_colwidth', None)

phone_id = random.choice(phone_ids)
conversation_files = [file for file in os.listdir('conversations') if f'phone_id_{phone_id}' in file]
conversation_file = random.choice(conversation_files)
conversation_df = pd.read_json(f'conversations/{conversation_file}')
conversation_df

created_at  phone_id  origin type_message  \
0  2024-08-25 21:24:32.335     15394   agent         text   
1  2024-08-25 21:24:59.516     15394  client         text   
2  2024-08-25 21:25:28.254     15394  client         text   
3  2024-08-25 21:28:58.971     15394  client         text   
4  2024-08-25 21:29:07.565     15394  client        image   
5  2024-08-25 21:29:28.042     15394   agent         text   
6  2024-08-25 21:29:41.329     15394  client         text   
7  2024-08-25 21:29:46.349     15394  client         text   
8  2024-08-25 21:29:56.088     15394   agent         text   
9  2024-08-25 21:30:29.146     15394   agent        image   
10 2024-08-25 21:30:58.421     15394   agent         text   
11 2024-08-25 21:32:03.336     15394  client         text   
12 2024-08-25 21:32:17.818     15394  client         text   
13 2024-08-25 21:57:35.557     15394   agent         text   
14 2024-08-25 21:57:54.182     15394   agent         text   
15 2024-08-25 21:58:17.323     15394  client         text   
16 2024-08-25 21:58:22.296     15394  client         text   
17 2024-08-25 21:58:25.723     15394   agent         text   
18 2024-08-25 21:58:40.976     15394   agent         text   
19 2024-08-25 21:59:24.960     15394  client         text   
20 2024-08-25 22:00:02.835     15394  client        image   
21 2024-08-25 22:00:10.439     15394  client         text   
22 2024-08-25 22:13:03.011     15394   agent         text   
23 2024-08-25 22:14:07.808     15394  client        image   
24 2024-08-25 22:33:18.395     15394   agent         text   
25 2024-08-25 23:02:35.886     15394  client         text   
26 2024-08-25 23:20:40.387     15394   agent         text   
27 2024-08-26 02:51:09.343     15394   agent         note   
28 2024-08-26 02:51:09.363     15394   agent        event   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                 message  
0                                                                                                                                                                                                                                                                                                                                                                                                                        Hola Santiago! buenas tardes\nHabls con Cecilia, pediatra\n\ncomo esta Joaquin?  
1                                                                                                                                                                                                                                                                                                                                                                                                                                                                       Bien bien \n\nTengo una consulta  
2                                                                                                                                                                                                                                                                                                                                                                     Como sé yo que está muy caliente el bebé\n\nPorque aveces cuando lo ponemos sobre el pecho; él con ropa\n\nDespués está muy rojito  
3                                                                                                                                                                                                                            

### Labeling conversations
We will label the conversations based on the following rules:
- **0**: If the conversation mention fever
- **1**: If the pediatrician notes mention fever
- **-1**: If there is no mention of fever

In [ ]:
def label_conversations(conversations):
    labeled_conversations = []
    fever_keywords = ['fiebre', 'temperatura', 'calentura', 'febril']  # Keywords for fever

    for conversation in conversations:
        label = -1  # By default, no mention of fever
        fever_detected = any(conversation['message'].str.contains('|'.join(fever_keywords), case=False, na=False))

        if fever_detected:
            label = 0  # Fever mentioned but not yet diagnosed
            if any(
                (conversation['type_message'] == 'note') &
                (conversation['message'].str.contains('|'.join(fever_keywords), case=False, na=False))
            ):
                label = 1  # Fever diagnosis

        labeled_conversations.append((conversation, label))

    return labeled_conversations

# Create a folder of labeled conversations
if not os.path.exists('labeled_conversations'):
    os.makedirs('labeled_conversations')

for i, historic in enumerate(historics):
    conversations = split_conversations(historic)[0]
    
    labeled_conversations = label_conversations(conversations)
    phone_id = historic['phone_id'].iloc[0]
    for j, (conversation, label) in enumerate(labeled_conversations):
        conversation.to_json(f'labeled_conversations/phone_id_{phone_id}_conversation_{j}_label_{label}.json', orient='records')

print('Labeled conversations saved:', len(labeled_conversations))


## Analysis
Let's look at the distribution of the labels and the number of messages in each conversation.

### 📌 Distribution of rounds of conversation?

In [ ]:
# Load the labeled conversations
labeled_conversations = []
labeled_conversation_files = os.listdir('labeled_conversations')
for file in labeled_conversation_files:
    conversation_df = pd.read_json(f'labeled_conversations/{file}')
    label = int(file.split('_')[-1].split('.')[0])
    labeled_conversations.append((conversation_df, label))

print('Labeled conversations loaded:', len(labeled_conversations))

In [ ]:
# 📌 Pregunta: Distribution of rounds of conversation?

import matplotlib.pyplot as plt

# contar la catidad de conversaciones por historico
rounds = []
for conversation, label in labeled_conversations:
    rounds.append(len(conversation))

# Plot the distribution of rounds
plt.figure(figsize=(12, 6))  # Increase the width of the figure
plt.hist(rounds, bins=20, color='skyblue', edgecolor='black')
plt.title('Distribution of rounds of conversation')
plt.xlabel('Number of rounds')
plt.ylabel('Number of conversations')

# Add labels on top of each bar
counts, bins, patches = plt.hist(rounds, bins=20, color='skyblue', edgecolor='black')
for count, patch in zip(counts, patches):
    height = patch.get_height()
    plt.text(patch.get_x() + patch.get_width() / 2, height, int(height), ha='center', va='bottom')

# Add more ticks on the x-axis
plt.xticks(bins, rotation=45)

plt.show()

## 📌 Distribution of time span

In [ ]:
# Distribution of time span of conversations
def time_span(conversation):
    created_at = pd.to_datetime(conversation['created_at'])
    return (created_at.max() - created_at.min()).total_seconds() / 3600

# Calculate the time span for each conversation
time_spans = []
for conversation, label in labeled_conversations:
    time_spans.append(time_span(conversation))

# Plot the distribution of time spans
plt.figure(figsize=(12, 6))  # Increase the width of the figure
plt.hist(time_spans, bins=20, color='skyblue', edgecolor='black')
plt.title('Distribution of time span of conversations')
plt.xlabel('Time span (hours)')
plt.ylabel('Number of conversations')

# Add labels on top of each bar
counts, bins, patches = plt.hist(time_spans, bins=20, color='skyblue', edgecolor='black')
for count, patch in zip(counts, patches):
    height = patch.get_height()
    plt.text(patch.get_x() + patch.get_width() / 2, height, int(height), ha='center', va='bottom')

plt.show()


In [ ]:
# mirar conversaciones con time_span mayor a 5 horas
time_span_threshold = 5
for conversation, label in labeled_conversations:
    if time_span(conversation) > time_span_threshold:
        print(conversation[['created_at', 'message']])
        break

## 📌 Distribution of inter-message timing

In [ ]:
#📌 Pregunta: Distribution of inter-message timing

# Calculate the time between messages for each conversation
def inter_message_timing(conversation):
    created_at = pd.to_datetime(conversation['created_at'])
    return (created_at - created_at.shift()).dt.total_seconds().fillna(0)

# Calculate the inter-message timing for each conversation
inter_message_timings = []

for conversation, label in labeled_conversations:
    inter_message_timings.extend(inter_message_timing(conversation))

# Convert inter-message timings from seconds to minutes
inter_message_timings = [timing / 60 for timing in inter_message_timings]

# Plot the distribution of inter-message timings
plt.figure(figsize=(12, 6))  # Increase the width of the figure
plt.hist(inter_message_timings, bins=20, color='skyblue', edgecolor='black')
plt.title('Distribution of inter-message timings')
plt.xlabel('Time between messages (minutes)')
plt.ylabel('Number of messages')

# Add labels on top of each bar
counts, bins, patches = plt.hist(inter_message_timings, bins=20, color='skyblue', edgecolor='black')
for count, patch in zip(counts, patches):
    height = patch.get_height()
    plt.text(patch.get_x() + patch.get_width() / 2, height, int(height), ha='center', va='bottom')

# Add more ticks on the x-axis
plt.xticks(bins, rotation=45)

plt.show()

## Wordclouds

### Excluded messages in the process of conversation separation


Excluir todo lo que sea del bot.

In [ ]:
import spacy
from wordcloud import WordCloud
import matplotlib.pyplot as plt
import random

# Assuming excluded_messages is defined in a previous cell
if 'excluded_messages' not in globals():
    excluded_messages = []  # Define an empty list or load the actual data

# load excluded messages
excluded_messages = []
excluded_message_files = os.listdir('excluded_messages')
for file in excluded_message_files:
    excluded_df = pd.read_json(f'excluded_messages/{file}')
    excluded_messages.extend(excluded_df['message'])
    

# Take a sample of excluded messages
sample_size = 10000  # Define the sample size
excluded_sample = random.sample(excluded_messages, min(sample_size, len(excluded_messages)))

# Cargar el modelo de spaCy para español
nlp = spacy.load('es_core_news_sm')

# Tokenizar y eliminar stopwords
def preprocess_text(text):
    doc = nlp(text)
    tokens = [token.text for token in doc if not token.is_stop and not token.is_punct]
    return ' '.join(tokens)

# Filtrar valores None y combinar todos los mensajes excluidos en una sola cadena
excluded_text = ' '.join([preprocess_text(msg) for msg in excluded_sample if msg is not None])

# Crear el word cloud
wordcloud = WordCloud(width=800, height=400, background_color='white').generate(excluded_text)

# Mostrar el word cloud
plt.figure(figsize=(10, 6))
plt.imshow(wordcloud, interpolation='bilinear')
plt.axis('off')
plt.show()


### Included messages in the process of conversation separation

In [ ]:
import spacy
from wordcloud import WordCloud
import matplotlib.pyplot as plt
import random

# Assuming labeled_conversations is defined in a previous cell
if 'labeled_conversations' not in globals():
    labeled_conversations = []  # Define an empty list or load the actual data

# Combine all included messages into a single string
included_messages = []
for conversation, label in labeled_conversations:
    included_messages.extend(conversation['message'].dropna().tolist())

# Take a sample of included messages
sample_size = 5000  # Define the sample size
included_sample = random.sample(included_messages, min(sample_size, len(included_messages)))

# Cargar el modelo de spaCy para español
nlp = spacy.load('es_core_news_sm')

# Tokenizar y eliminar stopwords
def preprocess_text(text):
    doc = nlp(text)
    tokens = [token.text for token in doc if not token.is_stop and not token.is_punct]
    return ' '.join(tokens)

# Filtrar valores None y combinar todos los mensajes incluidos en una sola cadena
included_text = ' '.join([preprocess_text(msg) for msg in included_sample if msg is not None])

# Crear el word cloud
wordcloud = WordCloud(width=800, height=400, background_color='white').generate(included_text)

# Mostrar el word cloud
plt.figure(figsize=(10, 6))
plt.imshow(wordcloud, interpolation='bilinear')
plt.axis('off')
plt.show()

### Wordclouds by label

- **0**: If the conversation mention fever
- **1**: If the pediatrician notes mention fever
- **-1**: If there is no mention of fever

In [ ]:
import spacy
from wordcloud import WordCloud
import matplotlib.pyplot as plt
import random

# Assuming labeled_conversations is defined in a previous cell
if 'labeled_conversations' not in globals():
    labeled_conversations = []  # Define an empty list or load the actual data

# Cargar el modelo de spaCy para español
nlp = spacy.load('es_core_news_sm')

# Tokenizar y eliminar stopwords
def preprocess_text(text):
    doc = nlp(text)
    tokens = [token.text for token in doc if not token.is_stop and not token.is_punct]
    return ' '.join(tokens)

# Crear WordCloud por cada etiqueta
def generate_wordcloud_by_label(label, conversations, sample_size=3000):
    messages = [msg for convo, lbl in conversations if lbl == label for msg in convo['message'].dropna().tolist()]
    sample = random.sample(messages, min(sample_size, len(messages)))
    text = ' '.join([preprocess_text(msg) for msg in sample if msg is not None])
    
    wordcloud = WordCloud(width=800, height=400, background_color='white').generate(text)
    
    plt.figure(figsize=(10, 6))
    plt.imshow(wordcloud, interpolation='bilinear')
    plt.axis('off')
    plt.title(f'WordCloud for Label {label}')
    plt.show()

# Generar word clouds para etiquetas 1, 0, -1
generate_wordcloud_by_label(1, labeled_conversations)
generate_wordcloud_by_label(0, labeled_conversations)
generate_wordcloud_by_label(-1, labeled_conversations)

In [ ]:
# Check the distribution of labels
labels = [label for _, label in labeled_conversations]
label_counts = pd.Series(labels).value_counts()
print(label_counts)

# Plot the distribution of the three labels
import matplotlib.pyplot as plt

plt.bar(label_counts.index, label_counts.values)
plt.xticks([-1, 0, 1])
plt.xlabel('Label')
plt.ylabel('Count')
plt.title('Distribution of Labels')
plt.show()


In [ ]:
# Calculate the number of conversations per historic and the number of messages in each historic
historic_conversation_counts = [len(split_conversations(historic)) for historic in historics]
historic_message_counts = [len(historic) for historic in historics]

# Create a DataFrame for plotting
historic_stats_df = pd.DataFrame({
    'historic_conversation_count': historic_conversation_counts,
    'historic_message_count': historic_message_counts
})

# Plot the data
plt.scatter(historic_stats_df['historic_message_count'], historic_stats_df['historic_conversation_count'])
plt.xlabel('Number of Messages in Historic')
plt.ylabel('Number of Conversations in Historic')
plt.title('Number of Conversations vs. Number of Messages in Historic')
plt.show()

## LDA

distribuir conversaciones a lo largo de los phone_ids existentes

In [ ]:
import pandas as pd
import spacy
from gensim import corpora
from gensim.models import LdaModel
import pyLDAvis.gensim_models as gensimvis
import pyLDAvis
import os
from IPython.display import display, HTML

# Cargar el modelo de spaCy para inglés
nlp = spacy.load('es_core_news_sm')

def preprocess_text_spacy(text):
    # Procesar el texto con spaCy
    doc = nlp(text.lower())
    # Filtrar tokens: eliminar stopwords, puntuación y lematizar
    tokens = [token.lemma_ for token in doc if not token.is_stop and token.is_alpha]
    return tokens

def lda_on_conversations_spacy(conversations, num_topics=5, passes=10):
    # Preprocesar todas las conversaciones
    processed_conversations = []
    for df in conversations:
        conversation = ' '.join(df['message'].tolist())
        processed_conversations.append(preprocess_text_spacy(conversation))
    
    # Crear diccionario y corpus
    dictionary = corpora.Dictionary(processed_conversations)
    corpus = [dictionary.doc2bow(text) for text in processed_conversations]
    
    # Entrenar el modelo LDA
    lda_model = LdaModel(corpus, num_topics=num_topics, id2word=dictionary, passes=passes)
    
    # Visualizar los temas
    vis_data = gensimvis.prepare(lda_model, corpus, dictionary)
    display(HTML(pyLDAvis.prepared_data_to_html(vis_data)))
    
    return lda_model

# Ejemplo de uso
# conversations es una lista de dataframes, donde cada df es una conversación
# Load labeled conversations
conversations = []
labels_to_load = {1: 100, 0: 100, -1: 100}
loaded_counts = {1: 0, 0: 0, -1: 0}

for file in labeled_conversation_files:
    if all(count >= labels_to_load[label] for label, count in loaded_counts.items()):
        break
    conversation_df = pd.read_json(f'labeled_conversations/{file}')
    label = int(file.split('_')[-1].split('.')[0])
    if loaded_counts[label] < labels_to_load[label]:
        conversations.append(conversation_df)
        loaded_counts[label] += 1

# Nonetype object reemplazado por string vacío
for i, conversation in enumerate(conversations):
    conversations[i] = conversation.fillna('')

print('Conversations loaded:', len(conversations))

# Solo pasar las primeras 60 conversaciones para acelerar el proceso
lda_model = lda_on_conversations_spacy(conversations, num_topics=5, passes=10)

## Pares preguntas-respuestas: Intento 1

In [5]:
import pandas as pd
import os
from itertools import groupby

# Cargar las conversaciones etiquetadas
labeled_conversations = []
labeled_conversation_files = os.listdir('labeled_conversations')
for file in labeled_conversation_files:
    conversation_df = pd.read_json(f'labeled_conversations/{file}')
    label = int(file.split('_')[-1].split('.')[0])  # Extraer etiqueta de fiebre
    labeled_conversations.append((conversation_df, label))

# Función para agrupar mensajes en bloques de pregunta y respuesta
def extract_qa_pairs(conversation, label, time_threshold=300):
    """
    Extrae pares pregunta-respuesta de una conversación.
    
    - Agrupa preguntas consecutivas del usuario como una sola pregunta.
    - Toma la primera respuesta del pediatra después de un bloque de pregunta.
    - Usa un umbral de tiempo (en segundos) para definir el fin de una pregunta.
    
    Retorna una lista de diccionarios con pregunta, respuesta y etiqueta.
    """
    qa_pairs = []
    current_question = []
    last_timestamp = None
    waiting_for_answer = False
    
    for index, row in conversation.iterrows():
        try:
            created_at = pd.to_datetime(row['created_at'])
            origin = row['origin']
            message = row['message']
            
            if origin == 'client':  # Agrupar preguntas del usuario
                if waiting_for_answer and current_question:
                    qa_pairs.append({
                        'pregunta': ' '.join(current_question),
                        'respuesta': None,
                        'etiqueta': label
                    })
                    current_question = []
                    waiting_for_answer = False
                
                if not last_timestamp or (created_at - last_timestamp).total_seconds() <= time_threshold:
                    current_question.append(message)
                else:
                    if current_question:
                        qa_pairs.append({
                            'pregunta': ' '.join(current_question),
                            'respuesta': None,
                            'etiqueta': label
                        })
                    current_question = [message]
                
                last_timestamp = created_at
                waiting_for_answer = True
            
            elif origin == 'agent' and waiting_for_answer and qa_pairs:  # Detectar respuesta del pediatra
                if current_question:
                    qa_pairs[-1]['respuesta'] = message
                    waiting_for_answer = False
        except Exception as e:
            print(f"Error procesando mensaje {index}: {e}")
    
    return qa_pairs

# Aplicar la extracción en todas las conversaciones
qa_dataset = []
for conversation, label in labeled_conversations:
    try:
        qa_dataset.extend(extract_qa_pairs(conversation, label))
    except Exception as e:
        print(f"Error procesando conversación con etiqueta {label}: {e}")

# Convertir a DataFrame y guardar
qa_df = pd.DataFrame(qa_dataset)
qa_df.dropna(subset=['respuesta'], inplace=True)  # Filtrar pares sin respuesta
qa_df.to_csv('qa_pairs.csv', index=False)

print(f"Pares pregunta-respuesta extraídos: {len(qa_df)}")



Error procesando mensaje 15: sequence item 3: expected str instance, NoneType found
Error procesando mensaje 16: sequence item 3: expected str instance, NoneType found
Error procesando mensaje 17: sequence item 3: expected str instance, NoneType found
Error procesando mensaje 19: sequence item 3: expected str instance, NoneType found
Error procesando mensaje 20: sequence item 3: expected str instance, NoneType found
Error procesando mensaje 21: sequence item 1: expected str instance, NoneType found
Error procesando mensaje 22: sequence item 1: expected str instance, NoneType found
Error procesando mensaje 23: sequence item 1: expected str instance, NoneType found
Error procesando mensaje 25: sequence item 1: expected str instance, NoneType found
Error procesando mensaje 28: sequence item 1: expected str instance, NoneType found
Error procesando mensaje 29: sequence item 1: expected str instance, NoneType found
Error procesando mensaje 31: sequence item 1: expected str instance, NoneTyp

In [6]:
qa_df.head(30)

pregunta  \
3                       Ya estamos llamando un médico   
4   Pero es por plan complementario y es médico ge...   
6                                            No señor   
7             Pero podemos pedir Acabo de vomitar más   
8   Y tiene 37,4 Recomiendas llevarla a la clínica...   
9                                     Y la febrícula?   
11   Doc, y en tabletas como hago para que se la tome   
13                                       Hace 15 días   
23                                               Max…   
24               Y cada cuánto se le da esta tableta?   
25  Muchas gracias doctor, la vino a ver un médico...   
33  Eso si me preocupa, por ejemplo ahora acabo de...   
34                   Y la cambié hace menos de 1 hora   
36                   Y la deposición es más abundante   
42                              Creo que tiene cólico   
44                        Acetaminophen le di a las 8   
50                                             3,4 cc   
55     Y hasta cuando le doy el acetaminophen a horas   
57       Le damos hasta donde quiera y solo líquidos?   
58                                       Y si vomita?   
60                           Vale doc, muchas gracias   
61              hasta cuando le sigo dando el sulzic?   
63                                     Doc, perdóname   
65                          No hay lío con darle más?   
67      Desde el domingo por la noche hasta el jueves   
68                               4… Vale doc, gracias   
73                                       Por la nariz   
75                            Es que es muy delicada…   
76              Ayer le aplicamos yerbabuena Almuerzo   
77  Almipro Garcias doc! Ay gracias doc! Es que es...   

                                            respuesta  etiqueta  
3   Diana  cuentame , cual es el nombre y la fecha...         0  
4                              tienes suero en casa ?         0  
6                       si , vamos a pedir suero oral         0  
7   vamos a intentar este como medida para control...         0  
8   la causa mas probable de todo es que sea un vi...         0  
9   Diana , si no logramos ni darle el medicamento...         0  
11                                 recuerdame el peso         0  
13  la tableta de 4 mg , la disolvemos en 4 m de a...         0  
23  Diana son 4 ml de agua, que en la jeringa son ...         0  
24  {Docochat} ha asignado esta conversación a {Ma...         0  
25                                          Perfecto!         0  
33                        Ok como ha tomado líquidos?         0  
34  {Docochat} ha asignado esta conversación a {Ar...         0  
36                        tiene sangre la deposicion?         0  
42       tienes acetaminofen en casa? dolex children?         0  
44                cuanto le diste y cuanto pesa ella?         0  
50  perfecto, esta bien la dosis, deja mas o menos...         1  
55                claro que si estamos muy pendientes         1  
57  exactamente sin forzar, despues cuando este me...        -1  
58   podriamos administrar medicamento para el vomito        -1  
60                                 completale 10 dias        -1  
61          con mucho gusto, estaremos muy pendientes        -1  
63  es de esperarse tambien que tenga gases y se d...        -1  
65                                       No tranquila         1  
67             Listo dáselo porque le duele pobrecito         1  
68  El 29 febrícula. posteriormente diarrea por lo...         1  
73  Puede ser un vasito que se reventó y no es gra...         0  
75                       Que cremas usas normalmente?        -1  
76     Intentalo. Vas a ver que le ayudaran un monton        -1  
77                                                 =)        -1

## Pares preguntas-respuestas: Intento 2 -- Mejora en agrupación preguntas - respuestas usando umbrales de tiempo y filtrando respuestas para evitar información incompleta

In [1]:
import pandas as pd
import os

# Cargar las conversaciones etiquetadas
labeled_conversations = []
labeled_conversation_files = os.listdir('labeled_conversations')
for file in labeled_conversation_files:
    conversation_df = pd.read_json(f'labeled_conversations/{file}')
    label = int(file.split('_')[-1].split('.')[0])  # Extraer etiqueta de fiebre
    labeled_conversations.append((conversation_df, label))

# Función para extraer pares pregunta-respuesta
def extract_qa_pairs(conversation, label, time_threshold=90):
    """
    Extrae pares pregunta-respuesta de una conversación.
    - Agrupa preguntas consecutivas del usuario en un solo bloque.
    - Detecta respuestas del pediatra y las agrupa si son consecutivas.
    - Filtra pares que no tienen una respuesta clara.
    """
    qa_pairs = []
    current_question = []
    last_timestamp = None
    waiting_for_answer = False
    current_response = []
    
    for index, row in conversation.iterrows():
        try:
            created_at = pd.to_datetime(row['created_at'])
            origin = row['origin']
            message = row['message']
            
            # Agrupar preguntas consecutivas del usuario
            if origin == 'client':
                if not last_timestamp or (created_at - last_timestamp).total_seconds() <= time_threshold: # Si el tiempo entre mensajes es corto, se agrupan
                    current_question.append(message)
                else: # Si hay una pausa, se considera una nueva pregunta
                    if current_question:
                        qa_pairs.append({'pregunta': ' '.join(current_question), 'respuesta': None, 'etiqueta': label})
                    current_question = [message]
                last_timestamp = created_at
                waiting_for_answer = True
            
            # Detectar respuestas del pediatra
            elif origin == 'agent' and waiting_for_answer:
                if current_question: # Si hay una pregunta pendiente, se asocia con la respuesta
                    if not current_response: # Si no hay respuestas previas, se agrega directamente
                        current_response.append(message)
                    else:
                        # Si el tiempo entre respuestas del pediatra es corto, se agrupan en un solo bloque
                        if (created_at - last_timestamp).total_seconds() <= time_threshold:
                            current_response.append(message)
                        else: # Si hay una pausa, se considera una nueva respuesta
                            qa_pairs[-1]['respuesta'] = ' '.join(current_response)
                            current_response = [message]
                    last_timestamp = created_at
                    waiting_for_answer = False
        except Exception as e:
            print(f"Error procesando mensaje {index}: {e}")
    
    # Asignar la última respuesta acumulada a la pregunta
    if current_question and current_response:
        qa_pairs.append({'pregunta': ' '.join(current_question), 'respuesta': ' '.join(current_response), 'etiqueta': label})
    
    return qa_pairs

# Aplicar la extracción a todas las conversaciones
qa_dataset = []
for conversation, label in labeled_conversations:
    try:
        qa_dataset.extend(extract_qa_pairs(conversation, label))
    except Exception as e:
        print(f"Error procesando conversación con etiqueta {label}: {e}")

# Convertir a DataFrame y guardar
qa_df = pd.DataFrame(qa_dataset)
qa_df.dropna(subset=['respuesta'], inplace=True)  # Filtrar pares sin respuesta
qa_df.to_csv('qa_pairs.csv', index=False)

print(f"Pares pregunta-respuesta extraídos: {len(qa_df)}")


Error procesando mensaje 10: list index out of range
Error procesando mensaje 8: list index out of range
Error procesando mensaje 9: list index out of range
Error procesando mensaje 10: list index out of range
Error procesando mensaje 16: list index out of range
Error procesando mensaje 17: list index out of range
Error procesando mensaje 19: sequence item 8: expected str instance, NoneType found
Error procesando mensaje 20: sequence item 8: expected str instance, NoneType found
Error procesando conversación con etiqueta 0: sequence item 8: expected str instance, NoneType found
Error procesando mensaje 13: list index out of range
Error procesando mensaje 25: sequence item 3: expected str instance, NoneType found
Error procesando mensaje 28: sequence item 3: expected str instance, NoneType found
Error procesando mensaje 29: sequence item 3: expected str instance, NoneType found
Error procesando mensaje 31: sequence item 3: expected str instance, NoneType found
Error procesando mensaje 3

In [4]:
pd.set_option('display.max_colwidth', None)
qa_df.head(30)

pregunta  \
0   Dr buenas tardes Mi bebé acaba de vomitar y hoy casi no ha querido comer Está con febrícula de 37 Ya estamos llamando un médico Pero es por plan complementario y es médico general Doc Fue hace media hora, pero siguió vomitando. Ya ha vomitado como seis veces. fecha de nacimiento. Veinte de junio del dos mil veintitrés. Ella tiene un año pasaditos en la deposición. No? Esta mañana hizo normal y no ha vuelto a ser, pero tampoco ha querido tomar mucho líquido y no ha querido comer mucho. Y ahorita vomito una cantidad de veces. No sé si me recomiendas llevarla a la clínica.   
3                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                   8,3 Hace 15 días   
10                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                         Le pedí el de 60 más Max…   
11                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              Y cada cuánto se le da esta tableta?   
13                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                           Six Doc   
15                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              Mejor Ya ha tomado más Y la deposición es más abundante Y más espesa   
16                                                                                                                                                                                                                                                                                                                                                                                                                                               Doc No Pero está llorando Después de comer Creo que

## Pares preguntas-respuestas: Intento 3
Extrae pares pregunta-respuesta de una conversación.
- Agrupa preguntas consecutivas del usuario en un solo bloque.
- Detecta respuestas del pediatra y las agrupa si son consecutivas.
- Filtra pares que no tienen una respuesta clara.
- Excluye mensajes de sistema y eventos automáticos.

In [4]:
import pandas as pd
import os

# Cargar las conversaciones etiquetadas
labeled_conversations = []
labeled_conversation_files = os.listdir('labeled_conversations')
for file in labeled_conversation_files:
    conversation_df = pd.read_json(f'labeled_conversations/{file}')
    label = int(file.split('_')[-1].split('.')[0])  # Extraer etiqueta de fiebre
    labeled_conversations.append((conversation_df, label))

# Función para extraer pares pregunta-respuesta
def extract_qa_pairs(conversation, label, time_threshold=90):
    """
    Extrae pares pregunta-respuesta de una conversación.
    - Agrupa preguntas consecutivas del usuario en un solo bloque.
    - Detecta respuestas del pediatra y las agrupa si son consecutivas.
    - Filtra pares que no tienen una respuesta clara.
    - Excluye mensajes de sistema y eventos automáticos.
    """
    qa_pairs = []
    current_question = []
    last_timestamp = None
    waiting_for_answer = False
    current_response = []
    
    for index, row in conversation.iterrows():
        try:
            created_at = pd.to_datetime(row['created_at'])
            origin = row['origin']
            message = row['message']
            
            # Ignorar eventos del sistema o mensajes vacíos
            if row['type_message'] in ['event', 'note'] or not isinstance(message, str) or message.strip() == "":
                continue
            
            # Agrupar preguntas consecutivas del usuario
            if origin == 'client':
                if not last_timestamp or (created_at - last_timestamp).total_seconds() <= time_threshold:
                    current_question.append(message)
                else:
                    if current_question:
                        qa_pairs.append({'pregunta': ' '.join(current_question), 'respuesta': None, 'etiqueta': label})
                    current_question = [message]
                last_timestamp = created_at
                waiting_for_answer = True
            
            # Detectar respuestas del pediatra
            elif origin == 'agent' and waiting_for_answer:
                if current_question:
                    if not current_response:
                        current_response.append(message)
                    else:
                        # Si el tiempo entre respuestas del pediatra es corto, se agrupan en un solo bloque
                        if (created_at - last_timestamp).total_seconds() <= time_threshold:
                            current_response.append(message)
                        else:
                            qa_pairs[-1]['respuesta'] = ' '.join(current_response)
                            current_response = [message]
                    last_timestamp = created_at
                    waiting_for_answer = False
        except Exception as e:
            print(f"Error procesando mensaje {index}: {e}")
    
    # Asignar la última respuesta acumulada a la pregunta
    if current_question and current_response:
        qa_pairs.append({'pregunta': ' '.join(current_question), 'respuesta': ' '.join(current_response), 'etiqueta': label})
    
    return qa_pairs

# Aplicar la extracción a todas las conversaciones
qa_dataset = []
for conversation, label in labeled_conversations:
    try:
        qa_dataset.extend(extract_qa_pairs(conversation, label))
    except Exception as e:
        print(f"Error procesando conversación con etiqueta {label}: {e}")

# Convertir a DataFrame y guardar
qa_df = pd.DataFrame(qa_dataset)
qa_df.dropna(subset=['respuesta'], inplace=True)  # Filtrar pares sin respuesta
qa_df.to_csv('qa_pairs.csv', index=False)

print(f"Pares pregunta-respuesta extraídos: {len(qa_df)}")


Error procesando mensaje 10: list index out of range
Error procesando mensaje 13: list index out of range
Error procesando mensaje 6: list index out of range
Error procesando mensaje 7: list index out of range
Error procesando mensaje 9: list index out of range
Error procesando mensaje 6: list index out of range
Error procesando mensaje 12: list index out of range
Error procesando mensaje 20: list index out of range
Error procesando mensaje 5: list index out of range
Error procesando mensaje 6: list index out of range
Error procesando mensaje 5: list index out of range
Error procesando mensaje 3: list index out of range
Error procesando mensaje 6: list index out of range
Error procesando mensaje 9: list index out of range
Error procesando mensaje 6: list index out of range
Error procesando mensaje 7: list index out of range
Error procesando mensaje 5: list index out of range
Error procesando mensaje 19: list index out of range
Error procesando mensaje 8: list index out of range
Error p

In [2]:
qa_df.head(30)

pregunta  \
0   Dr buenas tardes Mi bebé acaba de vomitar y ho...   
3                                    8,3 Hace 15 días   
10                          Le pedí el de 60 más Max…   
11               Y cada cuánto se le da esta tableta?   
13                                            Six Doc   
15  Mejor Ya ha tomado más Y la deposición es más ...   
16  Doc No Pero está llorando Después de comer Cre...   
18  Vale doc, es decir que si de acá al viernes si...   
19  Vale doc, si señora, pues ya está todo bien so...   
20  Vale doc y le doy el von si vomita más de una ...   
23    Doc, perdóname Es normal que tenga tantos gases   
24  No señora No hay lío con darle más? Como tomo ...   
26        Gracias doc Cualquier cosa les voy contando   
28  Almuerzo Almipro Garcias doc! Ay gracias doc! ...   
29  Doc, buenas noches Mi bebé de 14 meses tiene f...   
30  Hoy a las 5 Cada cuanto le doy el acetaminophe...   
32                                              Vale!   
36  Doc Me está subiendo la fiebre Le * 38.4 5:50 ...   
37  Doc, estoy pidiendo el médico, pero es general...   
40  Seguiría solo con el acetaminophen verdad? Se ...   
41                                       Gracias doc!   
43  Aunque la tos ee le escucha seca Es decir que ...   
44  Si señora con este Este Le hice esta mañana Es...   
46                                 Gracias doc? Doc!*   
50                                                  🙏   
51  Buenas noches Gracias! Doc! Una pregunta… es q...   
52  Le estoy dando Engystol, le puedo seguir dando...   
53                      Vale doc! Muchas gracias ☺️🙏🏻   
54  Buenas noches Ahora tiene soltura Sentimos un ...   
55  Gracia doc, en este momento está dormida… está...   

                                            respuesta  etiqueta  
0   la causa mas probable de todo es que sea un vi...         0  
3   Diana , si no logramos ni darle el medicamento...         0  
10  la tableta de 4 mg , la disolvemos en 4 m de a...         0  
11  Diana son 4 ml de agua, que en la jeringa son ...         0  
13                                          Perfecto!         0  
15       tienes acetaminofen en casa? dolex children?         0  
16                cuanto le diste y cuanto pesa ella?         0  
18  perfecto, esta bien la dosis, deja mas o menos...         1  
19  exactamente sin forzar, despues cuando este me...        -1  
20   podriamos administrar medicamento para el vomito        -1  
23  completale 10 dias con mucho gusto, estaremos ...        -1  
24  No tranquila Listo dáselo porque le duele pobr...         1  
26  Es la primera vez que le pasa? Y se demoro muc...         0  
28  Que cremas usas normalmente? Si esta muy bien....        -1  
29  le empezo la fiebre cuando? dificultad para re...         1  
30  Diana por los sintomas y a edad de Luciana, lo...         1  
32  la dosis de dolex para ella es 4 ml cada 6 hor...         1  
36  Si diana, no pasa nada, igual es momentaneo\ns...         1  
37  realmente podrias la ducha de agua tibia , com...         1  
40  no pasa nada , al ser medicamentos con mecanis...         1  
41                                 con el mayor gusto         1  
43  Esperemos que la fiebre siga mejorando, es muy...         1  
44  Ese esta perfecto , pero puedes incluso cada 4...         1  
46          esperar , darle un tiempito de eevolucion         1  
50  Luciana si?\nTiene 15 meses verdad? Vale diana...         0  
51  Diani lo más probable es que esté iniciando un...        -1  
52  Si, lo pueden sacar.   El viento no lo empeora...        -1  
53                                  Con mucho gusto 🤍        -1  
54  Para los síntomas tenemos algunas opciones, te...        -1  
55  si lo puedes iniciar mañana si lech esta perfe...        -1

## Pares preguntas-respuestas: Intento 4

In [ ]:
import pandas as pd
import os
import spacy
from sklearn.feature_extraction.text import TfidfVectorizer
from sentence_transformers import SentenceTransformer
import numpy as np
import torch

# Cargar modelo de embeddings para evaluar relevancia semántica
nlp = spacy.load("es_core_news_md")
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
embedder = SentenceTransformer("sentence-transformers/paraphrase-multilingual-MiniLM-L12-v2", device=device)

# Cargar las conversaciones etiquetadas
labeled_conversations = []
labeled_conversation_files = os.listdir('labeled_conversations')
for file in labeled_conversation_files:
    conversation_df = pd.read_json(f'labeled_conversations/{file}')
    label = int(file.split('_')[-1].split('.')[0])  # Extraer etiqueta de fiebre
    labeled_conversations.append((conversation_df, label))

# Función para extraer pares pregunta-respuesta
def extract_qa_pairs(conversation, label, time_threshold=90):
    """
    Extrae pares pregunta-respuesta de una conversación.
    - Agrupa preguntas consecutivas del usuario en un solo bloque.
    - Detecta respuestas del pediatra y las agrupa si son consecutivas.
    - Filtra pares que no tienen una respuesta clara.
    - Excluye mensajes de sistema y eventos automáticos.
    """
    qa_pairs = []
    current_question = []
    last_timestamp = None
    waiting_for_answer = False
    current_response = []
    
    for index, row in conversation.iterrows():
        try:
            created_at = pd.to_datetime(row['created_at'])
            origin = row['origin']
            message = row['message']
            
            # Ignorar eventos del sistema o mensajes vacíos
            if row['type_message'] in ['event', 'note'] or not isinstance(message, str) or message.strip() == "":
                continue
            
            # Agrupar preguntas consecutivas del usuario
            if origin == 'client':
                if not last_timestamp or (created_at - last_timestamp).total_seconds() <= time_threshold:
                    current_question.append(message)
                else:
                    if current_question:
                        qa_pairs.append({'pregunta': ' '.join(current_question), 'respuesta': None, 'etiqueta': label})
                    current_question = [message]
                last_timestamp = created_at
                waiting_for_answer = True
            
            # Detectar respuestas del pediatra
            elif origin == 'agent' and waiting_for_answer:
                if current_question:
                    if not current_response:
                        current_response.append(message)
                    else:
                        # Si el tiempo entre respuestas del pediatra es corto, se agrupan en un solo bloque
                        if (created_at - last_timestamp).total_seconds() <= time_threshold:
                            current_response.append(message)
                        else:
                            qa_pairs[-1]['respuesta'] = ' '.join(current_response)
                            current_response = [message]
                    last_timestamp = created_at
                    waiting_for_answer = False
        except Exception as e:
            print(f"Error procesando mensaje {index}: {e}")
    
    # Asignar la última respuesta acumulada a la pregunta
    if current_question and current_response:
        qa_pairs.append({'pregunta': ' '.join(current_question), 'respuesta': ' '.join(current_response), 'etiqueta': label})
    
    return qa_pairs

# Función para extraer la pregunta más relevante con embeddings y TF-IDF
def get_most_relevant_question(questions):
    if not questions:
        return None
    
    # Generar embeddings para cada pregunta
    embeddings = embedder.encode(questions)
    
    # Calcular la similitud de cada pregunta con la media del conjunto (pregunta más central)
    mean_embedding = np.mean(embeddings, axis=0)
    similarities = np.dot(embeddings, mean_embedding) / (np.linalg.norm(embeddings, axis=1) * np.linalg.norm(mean_embedding))
    
    # Seleccionar la pregunta más relevante (la más cercana al centro de masa del significado del conjunto)
    most_relevant_idx = np.argmax(similarities)
    return questions[most_relevant_idx]

# Aplicar la extracción a todas las conversaciones
qa_dataset = []
most_relevant_questions = []

for conversation, label in labeled_conversations:
    try:
        pairs = extract_qa_pairs(conversation, label)
        qa_dataset.extend(pairs)
        
        # Imprimir los pares pregunta-respuesta
        for pair in pairs:
            print(f"Pregunta: {pair['pregunta']}")
            print(f"Respuesta: {pair['respuesta']}")
            print(f"Etiqueta: {pair['etiqueta']}")
            print("------")
        
        # Extraer la pregunta más relevante de la conversación
        questions = [pair['pregunta'] for pair in pairs if pair['pregunta'] is not None]
        most_relevant_question = get_most_relevant_question(questions)
        most_relevant_questions.append({'pregunta_mas_relevante': most_relevant_question, 'etiqueta': label})
    except Exception as e:
        print(f"Error procesando conversación con etiqueta {label}: {e}")

# Convertir a DataFrame y guardar
qa_df = pd.DataFrame(qa_dataset)
qa_df.dropna(subset=['respuesta'], inplace=True)  # Filtrar pares sin respuesta
qa_df.to_csv('qa_pairs.csv', index=False)

relevant_q_df = pd.DataFrame(most_relevant_questions)
relevant_q_df.dropna(subset=['pregunta_mas_relevante'], inplace=True)
relevant_q_df.to_csv('relevant_questions.csv', index=False)

print(f"Pares pregunta-respuesta extraídos: {len(qa_df)}")
print(f"Preguntas más relevantes extraídas: {len(relevant_q_df)}")


c:\Users\alejo\OneDrive\Escritorio\practiceNLP\nlp_env\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


## Pares preguntas-respuestas: Intento 5

In [5]:
import pandas as pd
import os
import time

# Cargar las conversaciones etiquetadas
print("Cargando conversaciones etiquetadas...")
labeled_conversations = []
labeled_conversation_files = os.listdir('labeled_conversations')
for file in labeled_conversation_files:
    conversation_df = pd.read_json(f'labeled_conversations/{file}')
    label = int(file.split('_')[-1].split('.')[0])  # Extraer etiqueta de fiebre
    labeled_conversations.append((conversation_df, label))
print(f"Total de conversaciones cargadas: {len(labeled_conversations)}")

# Función para agrupar mensajes consecutivos del usuario en una pregunta coherente
def group_user_messages(conversation, time_threshold=60*5):
    """Agrupa mensajes consecutivos del usuario en bloques de preguntas."""
    grouped_messages = []
    current_question = []
    last_timestamp = None
    
    for _, row in conversation.iterrows():
        created_at = pd.to_datetime(row['created_at'])
        origin = row['origin']
        message = row['message']
        
        if origin == 'client':
            if not last_timestamp or (created_at - last_timestamp).total_seconds() <= time_threshold:
                current_question.append(message)
            else:
                if current_question:
                    grouped_messages.append(" ".join(current_question))
                current_question = [message]
            last_timestamp = created_at
        
    if current_question:
        grouped_messages.append(" ".join(current_question))
    
    return grouped_messages

# Función para detectar la primera respuesta del pediatra
def get_first_doctor_response(conversation, time_threshold=90):
    """Encuentra el primer bloque de respuesta del pediatra."""
    response_block = []
    found_response = False
    last_timestamp = None
    
    for _, row in conversation.iterrows():
        created_at = pd.to_datetime(row['created_at'])
        origin = row['origin']
        message = row['message']
        
        if origin == 'agent':
            if not found_response:
                response_block.append(message)
                found_response = True
            elif (created_at - last_timestamp).total_seconds() <= time_threshold:
                response_block.append(message)
            else:
                break
            last_timestamp = created_at
    
    return " ".join(response_block) if response_block else None

# Función para procesar cada conversación de manera interactiva
def debug_conversations(labeled_conversations, sample_size=5):
    """Muestra conversaciones una por una y permite analizar heurísticas en tiempo real."""
    for conversation, label in labeled_conversations[:sample_size]:
        print("\n" + "="*40)
        print(f"📌 Procesando nueva conversación (Etiqueta: {label})")
        print("="*40 + "\n")
        
        # Ordenar por timestamp y filtrar eventos del sistema
        conversation = conversation.sort_values(by='created_at')
        conversation = conversation[~conversation['type_message'].isin(['event', 'note'])]
        
        # Mostrar la conversación completa
        for _, row in conversation.iterrows():
            print(f"[{row['created_at']}] ({row['origin']}): {row['message']}")
        
        print("\n--- Aplicando heurísticas ---\n")
        
        # Extraer la primera pregunta y su respuesta
        first_question = group_user_messages(conversation)
        first_response = get_first_doctor_response(conversation)
        
        # Mostrar resultados
        print("📍 Pregunta detectada:")
        print(first_question[0] if first_question else "❌ No se encontró pregunta")
        print("\n📍 Respuesta detectada:")
        print(first_response if first_response else "❌ No se encontró respuesta")
        
        input("🔍 Presiona ENTER para continuar con la siguiente conversación...")
        time.sleep(1)

# Ejecutar la depuración interactiva
debug_conversations(labeled_conversations)


Cargando conversaciones etiquetadas...
Total de conversaciones cargadas: 5803

📌 Procesando nueva conversación (Etiqueta: 0)

[2024-06-29 21:45:10.281000] (client): Dr buenas tardes
[2024-06-29 21:45:22.120000] (client): Mi bebé acaba de vomitar y hoy casi no ha querido comer
[2024-06-29 21:45:33.120000] (client): Está con febrícula de 37
[2024-06-29 21:45:53.616000] (client): Ya estamos llamando un médico
[2024-06-29 21:46:07.245000] (client): Pero es por plan complementario y es médico general
[2024-06-29 21:50:10.810000] (agent): Diana  cuentame , cual es el nombre y la fecha de nacimiento de tu bebe ?
[2024-06-29 21:50:18.467000] (agent): hace cuanto fue el vomito ?
[2024-06-29 21:50:29.776000] (agent): ha tenido algun cambio en la deposicion ?
[2024-06-29 21:50:41.198000] (client): Doc Fue hace media hora, pero siguió vomitando. Ya ha vomitado como seis veces.
[2024-06-29 21:51:03.652000] (client): fecha de nacimiento. Veinte de junio del dos mil veintitrés. Ella tiene un año pasa

KeyboardInterrupt: Interrupted by user